In [3]:
import pandas as pd
import numpy as np
import requests
import json

# Function to get the postal code and geographical coordinates (latitude and longitude) of addresses

def find_postal(lst, filename):
    '''With the block number and street name, get the full address of the HDB flat,
    including the postal code, geographical coordinates (lat/long)'''
    
    # Iterate through the list of addresses
    for index, add in enumerate(lst):
        # Construct the URL to query the OneMap API for the address information
        url = "https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=" + add
        print(index, url)
        
        # Retrieve information from the website
        response = requests.get(url)
        try:
            # Parse the JSON response into a dictionary
            data = json.loads(response.text) 
        except ValueError:
            # Handle JSON decoding errors
            print('JSONDecodeError')
            pass
    
        # Convert the results from the JSON response into a DataFrame
        temp_df = pd.DataFrame.from_dict(data["results"])
        # Add the original address used in the search to the DataFrame
        temp_df["address"] = add
        
        # For the first address, initialize the file with the DataFrame
        if index == 0:
            file = temp_df
        else:
            # Append subsequent addresses' DataFrames to the file
            file = file.append(temp_df)
    
    # Save the combined DataFrame to a CSV file
    file.to_csv(filename + '.csv')

In [4]:
# Install the geopy package to calculate geographical distances
!pip install geopy

from geopy.distance import geodesic

def find_nearest(house, amenity, radius=1):
    """
    This function finds the nearest locations from the 'amenity' table relative to each address in the 'house' table.
    Both 'house' and 'amenity' are dataframes with a specific format:
        - 1st column: Any string column (e.g., addresses) taken from the "find_postal_address.py" output
        - 2nd column: Latitude (float)
        - 3rd column: Longitude (float)
    Column names do not matter.
    The function also counts the number of amenities within the specified radius (default=1 km).
    """
    results = {}  # Dictionary to store results for each house
    
    # Iterate through each house (address) in the 'house' dataframe
    for index, flat in enumerate(house.iloc[:,0]):
        
        # Extract the latitude and longitude for the current house
        flat_loc = (house.iloc[index,1], house.iloc[index,2])
        # Initialize a list to store details of the nearest amenity
        # ['house_address', 'nearest_amenity', 'min_distance', 'amenities_within_radius']
        flat_amenity = ['', '', 100, 0]  # Start with a large initial distance (100 km)
        
        # Iterate through each amenity in the 'amenity' dataframe
        for ind, eachloc in enumerate(amenity.iloc[:,0]):
            # Extract the latitude and longitude for the current amenity
            amenity_loc = (amenity.iloc[ind,1], amenity.iloc[ind,2])
            # Calculate the geodesic distance between the house and the amenity
            distance = geodesic(flat_loc, amenity_loc)
            distance = float(str(distance)[:-3])  # Convert distance to float (in kilometers)

            # Count the number of amenities within the specified radius
            if distance <= radius:
                flat_amenity[3] += 1

            # Update the nearest amenity if the current one is closer
            if distance < flat_amenity[2]:
                flat_amenity[0] = flat        # Update with house address
                flat_amenity[1] = eachloc     # Update with nearest amenity
                flat_amenity[2] = distance    # Update with the distance to the nearest amenity

        # Store the results for the current house in the dictionary
        results[flat] = flat_amenity
    
    return results  # Return the dictionary containing the nearest amenities and counts for each house

In [5]:
def dist_from_location(house, location):
    """
    This function calculates the distance of a given location from each address in the 'house' dataframe.
    
    Parameters:
    - house: DataFrame with the following format:
        1st column: Any string column (e.g., addresses) taken from the "find_postal_address.py" output.
        2nd column: Latitude (float)
        3rd column: Longitude (float)
      Note: The column names do not matter.
    - location: A tuple containing the latitude and longitude of the location to measure the distance from.
    
    Returns:
    - A dictionary where each key is an address from the 'house' dataframe, and the value is a list containing:
        [address, distance from the specified location]
    """
    results = {}  # Dictionary to store the results for each house
    
    # Iterate through each house (address) in the 'house' dataframe
    for index, flat in enumerate(house.iloc[:, 0]):
        
        # Extract the latitude and longitude for the current house
        flat_loc = (house.iloc[index, 1], house.iloc[index, 2])
        
        # Initialize a list to store the address and the calculated distance
        flat_amenity = ['', 100]  # Start with a large initial distance (100 km)
        
        # Calculate the geodesic distance between the house and the specified location
        distance = geodesic(flat_loc, location)
        distance = float(str(distance)[:-3])  # Convert the distance to float (in kilometers)
        
        # Update the list with the current house address and the calculated distance
        flat_amenity[0] = flat
        flat_amenity[1] = distance
        
        # Store the results in the dictionary
        results[flat] = flat_amenity
    
    return results  # Return the dictionary containing the distances for each house

In [6]:
# Load the dataset from the specified file path into a DataFrame named 'prices'
prices = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/output3.0 grouped region.csv')

# Display a concise summary of the DataFrame, including information about its columns,
# data types, and the number of non-null entries for each column
prices.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 932372 entries, 0 to 932371
Data columns (total 15 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   address              932372 non-null  object 
 1   month                932372 non-null  object 
 2   town                 932372 non-null  object 
 3   flat_type            932372 non-null  object 
 4   block                932372 non-null  object 
 5   street_name          932372 non-null  object 
 6   storey_range         932372 non-null  object 
 7   floor_area_sqm       932372 non-null  float64
 8   flat_model           932372 non-null  object 
 9   lease_commence_date  932372 non-null  int64  
 10  resale_price         932372 non-null  int64  
 11  remaining_lease      932372 non-null  int64  
 12  flat_group           932372 non-null  object 
 13  region               932372 non-null  object 
 14  mature               932372 non-null  object 
dtypes: float64(1), in

In [7]:
# Convert the 'address' column into a list containing all addresses
all_address = list(prices['address'])

# Create a list of unique addresses by converting 'all_address' to a set (which removes duplicates)
# and then back to a list
unique_address = list(set(all_address))

# Print the number of unique addresses found
print('Unique addresses:', len(unique_address))

# Print the entire DataFrame to see the data and the newly created 'address' column
print(prices)

# Print the column names of the DataFrame to check the structure and the addition of the 'address' column
print(prices.columns)

Unique addresses: 9841
                     address       month        town flat_type block  \
0       309 ang mo kio ave 1  1990-01-01  ang mo kio    1 room   309   
1       309 ang mo kio ave 1  1990-01-01  ang mo kio    1 room   309   
2       309 ang mo kio ave 1  1990-01-01  ang mo kio    1 room   309   
3       309 ang mo kio ave 1  1990-01-01  ang mo kio    1 room   309   
4       216 ang mo kio ave 1  1990-01-01  ang mo kio    3 room   216   
...                      ...         ...         ...       ...   ...   
932367     468a yishun st 43  2024-08-01      yishun    4 room  468a   
932368     640a yishun st 61  2024-08-01      yishun    4 room  640a   
932369      762 yishun st 72  2024-08-01      yishun    4 room   762   
932370      658 yishun ave 4  2024-08-01      yishun    5 room   658   
932371      860 yishun ave 4  2024-08-01      yishun    5 room   860   

             street_name storey_range  floor_area_sqm      flat_model  \
0       ang mo kio ave 1     10 to 12  

In [8]:
# Save the 'prices' DataFrame to a CSV file named 'flat_address.csv' at the specified file path
# The 'index=False' parameter ensures that the row index is not written to the CSV file
prices.to_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_address.csv', index=False)

In [9]:
# Call the 'find_postal' function with the list of unique addresses ('unique_address')
# and save the resulting data (including postal codes and geographical coordinates) 
# to a CSV file named 'flat_address.csv' in the specified directory.
find_postal(unique_address, 'C:/Users/Bwah/Desktop/488 Dataset/flat_address.csv')

0 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=580 woodlands dr 16
1 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=556 ang mo kio ave 10
2 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=226b compassvale walk
3 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=41 stirling rd


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


4 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=238 tampines st 21
5 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=217b boon lay ave
6 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=25 eunos cres
7 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=329 jurong east ave 1


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


8 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=764 choa chu kang nth 5
9 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=443d fajar rd
10 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=292b compassvale st
11 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=785c woodlands rise


...

9831 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=631 pasir ris dr 3
9832 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=425 bt batok west ave 2
9833 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=733 tampines st 71
9834 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=140 lor ah soo


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


9835 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=239 bishan st 22
9836 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=161 mei ling st
9837 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=427 hougang ave 6
9838 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=865 tampines st 83


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


9839 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=452b sengkang west way
9840 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=105 bishan st 12


In [10]:
# Load the dataset from the specified file path into a DataFrame named 'flat_coord'
# The dataset contains addresses along with postal codes and geographical coordinates
flat_coord = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_address.csv.csv')

# Select only the relevant columns: 'address', 'LATITUDE', and 'LONGITUDE'
# This keeps only the address and its associated latitude and longitude coordinates
flat_coord = flat_coord[['address', 'LATITUDE', 'LONGITUDE']]

# Display the first few rows of the updated DataFrame to check the data
flat_coord.head()

address  LATITUDE   LONGITUDE
0    580 woodlands dr 16  1.430584  103.796276
1    580 woodlands dr 16  1.430584  103.796276
2  556 ang mo kio ave 10  1.372032  103.857625
3  556 ang mo kio ave 10  1.372032  103.857625
4  226b compassvale walk  1.387712  103.899302

In [11]:
# Merge the 'prices' and 'flat_coord' DataFrames on the 'address' column
merged_df = prices.merge(flat_coord, on='address', how='left')

# Check for any rows where 'LATITUDE' or 'LONGITUDE' is missing
unmatched_addresses = merged_df[merged_df['LATITUDE'].isnull() | merged_df['LONGITUDE'].isnull()]

# Display the unmatched addresses
unmatched_addresses.head()

# Optionally, count the number of unmatched addresses
num_unmatched = unmatched_addresses.shape[0]
print(f"Number of unmatched addresses: {num_unmatched}")

Number of unmatched addresses: 0


In [12]:
# Load the dataset from the specified file path into a DataFrame named 'supermarket'
# The dataset contains information about supermarket licenses
supermarket = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/ListofSupermarketLicences.csv')

# Display the first few rows of the DataFrame to get an overview of the supermarket license data
supermarket.head()

licence_num                          licensee_name  \
0   S02185J000  COLD STORAGE SINGAPORE (1983) PTE LTD   
1   S97166P000  COLD STORAGE SINGAPORE (1983) PTE LTD   
2  CE15B61K000          U STARS SUPERMARKET PTE. LTD.   
3   S02029J000        NTUC Fairprice Co-operative Ltd   
4  CE04561V000        SHENG SIONG SUPERMARKET PTE LTD   

                 building_name block_house_num level_num unit_num  \
0                           na             982         1        1   
1  HOUGANG GREEN SHOPPING MALL              21         1       52   
2                           na             330         1        1   
3                HOUGANG POINT               1         2        1   
4                           na              19         1    42401   

                street_name postal_code  
0         BUANGKOK CRESCENT      530982  
1         HOUGANG STREET 51      538719  
2         ANCHORVALE STREET      540330  
3         HOUGANG STREET 91      538692  
4  SERANGOON NORTH AVENUE 5      554913

In [13]:
# Extract the 'postal_code' column from the 'supermarket' DataFrame into a list named 'supermarket_address'
# This list contains all postal codes for supermarkets
supermarket_address = list(supermarket['postal_code'])

# Create a list of unique postal codes by converting 'supermarket_address' to a set (which removes duplicates)
# and then converting it back to a list
unique_supermarket_address = list(set(supermarket_address))

# Print the number of unique postal codes found in the dataset
print('Unique addresses:', len(unique_supermarket_address))

Unique addresses: 445


In [14]:
# Call the 'find_postal' function with the list of unique supermarket postal codes ('unique_supermarket_address')
# and save the resulting data (including postal codes and geographical coordinates) 
# to a CSV file named 'ListofSupermarketLicences.csv' in the specified directory.
find_postal(unique_supermarket_address, 'C:/Users/Bwah/Desktop/488 Dataset/ListofSupermarketLicences.csv')

0 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=471739
1 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=659003
2 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=372018


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


3 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=609601
4 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=161026
5 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=823308
6 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=600037


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


7 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=486038
8 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=459125
9 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=760925
10 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=018987


...

C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


437 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=637734
438 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=520506
439 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=760293
440 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=278116


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


441 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=530642
442 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=640962
443 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=269707
444 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=820108


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


In [15]:
# Load the dataset from the specified file path into a DataFrame named 'supermarket_coord'
# This dataset contains information about supermarket locations, including postal codes and coordinates
supermarket_coord = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/ListofSupermarketLicences.csv.csv')

# Remove duplicate rows based on the 'POSTAL' column to ensure that each postal code is unique
supermarket_coord.drop_duplicates(subset=['POSTAL'], inplace=True)

# Select only the relevant columns: 'POSTAL', 'LATITUDE', and 'LONGITUDE'
# This keeps only the postal code and its associated latitude and longitude coordinates
supermarket_coord = supermarket_coord[['POSTAL', 'LATITUDE', 'LONGITUDE']]

# Display the first few rows of the updated DataFrame to check the data
supermarket_coord.head()

POSTAL  LATITUDE   LONGITUDE
0   471739  1.338242  103.923304
1   659003  1.365774  103.748521
7   372018  1.329181  103.888248
8   609601  1.334918  103.746877
14  161026  1.282634  103.825596

In [16]:
# Use the 'find_nearest' function to find the nearest supermarket for each flat in 'flat_coord'
# The function returns a dictionary where each key is a flat address and the value is information about the nearest supermarket
nearest_supermarket = find_nearest(flat_coord, supermarket_coord)

# Convert the dictionary returned by 'find_nearest' into a DataFrame
# The DataFrame is transposed to align the dictionary keys with DataFrame columns
flat_supermarket = pd.DataFrame.from_dict(nearest_supermarket).T

# Rename the columns of the DataFrame for better readability
# The columns are renamed to: 'flat', 'supermarket', 'supermarket_dist', and 'num_supermarket_2km'
flat_supermarket = flat_supermarket.rename(columns={0: 'flat', 1: 'supermarket', 2: 'supermarket_dist', 3: 'num_supermarket_2km'})

# Reset the index of the DataFrame and drop the old index column
flat_supermarket = flat_supermarket.reset_index().drop('index', axis=1)

# Display the first few rows of the DataFrame to review the data
flat_supermarket.head()

flat supermarket supermarket_dist num_supermarket_2km
0    580 woodlands dr 16      730548         0.246302                   3
1  556 ang mo kio ave 10      560525         0.411332                   3
2  226b compassvale walk      540118         0.385921                   6
3         41 stirling rd      141088         0.540076                   3
4     238 tampines st 21      520506         0.075366                   7

In [17]:
# Save the 'flat_supermarket' DataFrame to a CSV file named 'flat_supermarket.csv' at the specified file path
# The 'index=False' parameter ensures that the row index is not included in the output CSV file
flat_supermarket.to_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_supermarket.csv', index=False)

In [18]:
# Load the dataset from the specified file path into a DataFrame named 'school'
# The dataset contains general information about schools and uses 'cp1252' encoding to handle special characters
school = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/Generalinformationofschools.csv', encoding='cp1252')

# Display the first 10 rows of the DataFrame to review the structure and contents of the school information data
school.head(10)

school_name                            url_address  \
0           ADMIRALTY PRIMARY SCHOOL       https://admiraltypri.moe.edu.sg/   
1         ADMIRALTY SECONDARY SCHOOL     http://www.admiraltysec.moe.edu.sg   
2       AHMAD IBRAHIM PRIMARY SCHOOL  http://www.ahmadibrahimpri.moe.edu.sg   
3     AHMAD IBRAHIM SECONDARY SCHOOL  http://www.ahmadibrahimsec.moe.edu.sg   
4                     AI TONG SCHOOL           http://www.aitong.moe.edu.sg   
5           ALEXANDRA PRIMARY SCHOOL         http://alexandrapri.moe.edu.sg   
6        ANCHOR GREEN PRIMARY SCHOOL   http://www.anchorgreenpri.moe.edu.sg   
7            ANDERSON PRIMARY SCHOOL      http://www.andersonpri.moe.edu.sg   
8          ANDERSON SECONDARY SCHOOL      http://www.andersonsec.moe.edu.sg   
9  ANDERSON SERANGOON JUNIOR COLLEGE                   www.asrjc.moe.edu.sg   

                        address  postal_code telephone_no telephone_no_2  \
0         11   WOODLANDS CIRCLE       738907     63620598             na   
1       31   WOODLANDS CRESCENT       737916     63651733       63654596   
2         10   YISHUN STREET 11       768643     67592906             na   
3          751  YISHUN AVENUE 7       768928     67585384             na   
4        100  Bright Hill Drive       579646     64547672             na   
5  2A   Prince Charles Crescent       159016     62485400             na   
6         31   Anchorvale Drive       544969     68861356             na   
7         19   ANG MO KIO AVE 9       569785     64560340             na   
8     10   ANG MO KIO STREET 53       569206     64598303             na   
9      4500 ANG MO KIO AVENUE 6       569843     64596822             na   

     fax_no fax_no_2              email_address  \
0  63627512       na    ADMIRALTY_PS@MOE.EDU.SG   
1  63652774       na    Admiralty_SS@moe.edu.sg   
2  67592927       na            aips@moe.edu.sg   
3  67557778       na            aiss@moe.edu.sg   
4  64532726       na      AITONG_SCH@MOE.EDU.SG   
5  62485409       na    alexandra_ps@moe.edu.sg   
6  63159825       na  anchorgreen_ps@moe.edu.sg   
7  65522310       na     anderson_ps@moe.edu.sg   
8  64586104       na     anderson_ss@moe.edu.sg   
9  64598734       na           asrjc@moe.edu.sg   

                                 mrt_desc  ...   nature_code    session_code  \
0                       Admiralty Station  ...  CO-ED SCHOOL        FULL DAY   
1                           ADMIRALTY MRT  ...  CO-ED SCHOOL  SINGLE SESSION   
2                                  Yishun  ...  CO-ED SCHOOL  SINGLE SESSION   
3                CANBERRA MRT, YISHUN MRT  ...  CO-ED SCHOOL  SINGLE SESSION   
4                              Bishan MRT  ...  CO-ED SCHOOL  SINGLE SESSION   
5    Redhill Station  Tiong Bahru Station  ...  CO-ED SCHOOL  SINGLE SESSION   
6  MRT : NE16-Sengkang LRT : SW7-TongKang  ...  CO-ED SCHOOL  SINGLE SESSION   
7                Yio Chu Kang MRT Station  ...  CO-ED SCHOOL  SINGLE SESSION   
8        ANG MO KIO MRT, YIO CHU KANG MRT  ...  CO-ED SCHOOL  SINGLE SESSION   
9                Yio Chu Kang MRT Station  ...  CO-ED SCHOOL        FULL DAY   

   mainlevel_code sap_ind autonomous_ind gifted_ind ip_ind  \
0         PRIMARY      No             No         No     No   
1       SECONDARY      No             No         No     No   
2         PRIMARY      No             No         No     No   
3       SECONDARY      No             No         No     No   
4         PRIMARY     Yes             No         No     No   
5         PRIMARY      No             No         No     No   
6         PRIMARY      No             No         No     No   
7         PRIMARY      No             No         No     No   
8       SECONDARY      No            Yes         No     No   
9  JUNIOR COLLEGE      No             No         No     No   

   mothertongue1_code mothertongue2_code mothertongue3_code  
0             Chinese              Malay              Tamil  
1             Chinese              Malay              Tamil  
2     

In [19]:
# Extract the 'school_name' column from the 'school' DataFrame into a list named 'school_name'
# This list contains all school names from the dataset
school_name = list(school['school_name'])

# Create a list of unique school names by converting 'school_name' to a set (which removes duplicates)
# and then converting it back to a list
unique_school_name = list(set(school_name))

# Print the number of unique school names found in the dataset
print('Unique addresses:', len(unique_school_name))

Unique addresses: 337


In [20]:
# Call the 'find_postal' function with the list of unique school names ('unique_school_name')
# and save the resulting data (including postal codes and geographical coordinates) 
# to a CSV file named 'Generalinformationofschools.csv' in the specified directory.
find_postal(unique_school_name, 'C:/Users/Bwah/Desktop/488 Dataset/Generalinformationofschools.csv')

0 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=RED SWASTIKA SCHOOL
1 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=AHMAD IBRAHIM PRIMARY SCHOOL
2 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=CHRIST CHURCH SECONDARY SCHOOL
3 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=MAHA BODHI SCHOOL


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


4 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=ZHENGHUA SECONDARY SCHOOL
5 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=TECK WHYE PRIMARY SCHOOL
6 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=WHITE SANDS PRIMARY SCHOOL
7 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=ST. GABRIEL'S PRIMARY SCHOOL


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


8 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=QUEENSWAY SECONDARY SCHOOL
9 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=NORTH VIEW PRIMARY SCHOOL
10 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=PARK VIEW PRIMARY SCHOOL
11 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=KUO CHUAN PRESBYTERIAN PRIMARY SCHOOL


...

C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


328 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=CHIJ OUR LADY QUEEN OF PEACE
329 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BEACON PRIMARY SCHOOL
330 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=QIFA PRIMARY SCHOOL
331 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=CEDAR GIRLS' SECONDARY SCHOOL


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


332 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=RADIN MAS PRIMARY SCHOOL
333 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=METHODIST GIRLS' SCHOOL (PRIMARY)
334 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=MARYMOUNT CONVENT SCHOOL
335 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BUKIT PANJANG PRIMARY SCHOOL
336 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BUKIT VIEW SECONDARY SCHOOL


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


In [21]:
# Load the dataset from the specified file path into a DataFrame named 'school_coord'
# This dataset contains information about schools, including postal codes and coordinates
school_coord = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/Generalinformationofschools.csv.csv')

# Remove duplicate rows based on the 'POSTAL' column to ensure that each postal code is unique
school_coord.drop_duplicates(subset=['POSTAL'], inplace=True)

# Select only the relevant columns: 'address', 'LATITUDE', and 'LONGITUDE'
# This keeps only the address and its associated latitude and longitude coordinates
school_coord = school_coord[['address', 'LATITUDE', 'LONGITUDE']]

# Display the first few rows of the updated DataFrame to check the data
school_coord.head()

address  LATITUDE   LONGITUDE
0             RED SWASTIKA SCHOOL  1.334057  103.934318
2    AHMAD IBRAHIM PRIMARY SCHOOL  1.433153  103.832942
3  CHRIST CHURCH SECONDARY SCHOOL  1.426568  103.793451
4               MAHA BODHI SCHOOL  1.328580  103.901307
6               MAHA BODHI SCHOOL  1.328471  103.901299

In [22]:
# Use the 'find_nearest' function to find the nearest school for each flat in 'flat_coord'
# The function returns a dictionary where each key is a flat address and the value contains information about the nearest school
nearest_school = find_nearest(flat_coord, school_coord)

# Convert the dictionary returned by 'find_nearest' into a DataFrame
# The DataFrame is transposed to align the dictionary keys with DataFrame columns
flat_school = pd.DataFrame.from_dict(nearest_school).T

# Rename the columns of the DataFrame for better readability
# The columns are renamed to: 'flat', 'school', 'school_dist', and 'num_school_2km'
flat_school = flat_school.rename(columns={0: 'flat', 1: 'school', 2: 'school_dist', 3: 'num_school_2km'})

# Reset the index of the DataFrame and drop the old index column
flat_school = flat_school.reset_index().drop('index', axis=1)

# Display the first few rows of the DataFrame to review the data
flat_school.head()

flat                      school school_dist  \
0    580 woodlands dr 16  WOODGROVE SECONDARY SCHOOL    0.251862   
1  556 ang mo kio ave 10    JING SHAN PRIMARY SCHOOL    0.611724   
2  226b compassvale walk  SENG KANG SECONDARY SCHOOL    0.161496   
3         41 stirling rd  QUEENSWAY SECONDARY SCHOOL    0.177472   
4     238 tampines st 21  PASIR RIS SECONDARY SCHOOL    0.313643   

  num_school_2km  
0              8  
1              3  
2              9  
3              3  
4              7

In [23]:
# Save the 'flat_school' DataFrame to a CSV file named 'flat_school.csv' at the specified file path
# The 'index=False' parameter ensures that the row index is not included in the output CSV file
flat_school.to_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_school.csv', index=False)

In [24]:
# Load the dataset from the specified file path into a DataFrame named 'hawker'
# This dataset contains information about government markets and hawker centers
hawker = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/ListofGovernmentMarketsHawkerCentres.csv')

# Display the first 10 rows of the DataFrame to review the structure and contents of the hawker center data
hawker.head(10)

name_of_centre  \
0           Adam Road Food Centre   
1         Amoy Street Food Centre   
2               Bedok Food Centre   
3             Beo Crescent Market   
4              Berseh Food Centre   
5              Bukit Timah Market   
6         Chomp Chomp Food Centre   
7    Commonwealth Crescent Market   
8              Dunman Food Centre   
9  East Coast Lagoon Food Village   

                                  location_of_centre type_of_centre  \
0                            2, Adam Road, S(289876)             HC   
1  National Development Building, Annex B, Telok ...             HC   
2                           1, Bedok Road, S(469572)             HC   
3                       38A, Beo Crescent, S(169982)            MHC   
4                        166, Jalan Besar, S(208877)             HC   
5              51, Upper Bukit Timah Road, S(588215)            MHC   
6                20, Kensington Park Road, S(557269)             HC   
7               31, Commonwealth Crescent, S(149644)            MHC   
8                          271, Onan Road, S(424768)             HC   
9                1220, East Coast Parkway, S(468960)             HC   

        owner  no_of_stalls  no_of_cooked_food_stalls  \
0  Government            32                        32   
1  Government           135                       134   
2  Government            32                        32   
3  Government            94                        32   
4  Government            66                        66   
5  Government           179                        84   
6  Government            36                        36   
7  Government           102                        39   
8  Government            30                        30   
9  Government            63                        63   

   no_of_mkt_produce_stalls  
0                         0  
1                         1  
2                         0  
3                        62  
4                         0  
5                        95  
6                         0  
7                        63  
8                         0  
9                         0

In [25]:
# Extract the 'name_of_centre' column from the 'hawker' DataFrame into a list named 'hawker_name'
# This list contains all the names of the hawker centers from the dataset
hawker_name = list(hawker['name_of_centre'])

# Create a list of unique hawker center names by converting 'hawker_name' to a set (which removes duplicates)
# and then converting it back to a list
unique_hawker_name = list(set(hawker_name))

# Print the number of unique hawker center names found in the dataset
# This helps to determine how many distinct hawker centers are represented
print('Unique addresses:', len(unique_hawker_name))

Unique addresses: 107


In [26]:
# Call the 'find_postal' function with the list of unique hawker center names ('unique_hawker_name')
# and save the resulting data (including postal codes and geographical coordinates) 
# to a CSV file named 'ListofGovernmentMarketsHawkerCentres.csv' in the specified directory.
find_postal(unique_hawker_name, 'C:/Users/Bwah/Desktop/488 Dataset/ListofGovernmentMarketsHawkerCentres.csv')

0 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Tiong Bahru Market
1 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 7 Empress Road
2 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 724 Ang Mo Kio Ave 6
3 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 216 Bedok North Street 1


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


4 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blks 1A/ 2A/ 3A Commonwealth Drive
5 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 112 Jalan Bukit Merah
6 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 4A Jalan Batu
7 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 505 Jurong West Street 52


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


8 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Kovan Market & Food Centre
9 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 89 Circuit Road
10 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 93 Toa Payoh Lorong 4
11 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 84 Marine Parade Central


...

C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


99 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 1 Jalan Kukoh
100 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 75 Toa Payoh Lorong 5
101 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blks 79/79A Circuit Road
102 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Geylang Serai Market


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


103 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 448 Clementi Ave 3
104 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 85 Redhill Lane
105 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Blk 16 Bedok South Road
106 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Adam Road Food Centre


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


In [27]:
# Load the dataset from the specified file path into a DataFrame named 'hawker_coord'
# This dataset contains information about hawker centers, including postal codes and coordinates
hawker_coord = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/ListofGovernmentMarketsHawkerCentres.csv.csv')

# Remove duplicate rows based on the 'POSTAL' column to ensure that each postal code is unique
hawker_coord.drop_duplicates(subset=['POSTAL'], inplace=True)

# Select only the relevant columns: 'POSTAL', 'LATITUDE', and 'LONGITUDE'
# This keeps only the postal code and its associated latitude and longitude coordinates
hawker_coord = hawker_coord[['POSTAL', 'LATITUDE', 'LONGITUDE']]

# Display the first few rows of the updated DataFrame to check the data
hawker_coord.head()

POSTAL  LATITUDE   LONGITUDE
0  168898  1.284686  103.832422
2  268867  1.317250  103.805979
3  268868  1.317407  103.805812
4  268869  1.317135  103.805913
5  219428  1.307997  103.848209

In [28]:
# Use the 'find_nearest' function to find the nearest hawker center for each flat in 'flat_coord'
# The function returns a dictionary where each key is a flat address and the value contains information about the nearest hawker center
nearest_hawker = find_nearest(flat_coord, hawker_coord)

# Convert the dictionary returned by 'find_nearest' into a DataFrame
# The DataFrame is transposed to align the dictionary keys with DataFrame columns
flat_hawker = pd.DataFrame.from_dict(nearest_hawker).T

# Rename the columns of the DataFrame for better readability
# The columns are renamed to: 'flat', 'hawker', 'hawker_dist', and 'num_hawker_2km'
flat_hawker = flat_hawker.rename(columns={0: 'flat', 1: 'hawker', 2: 'hawker_dist', 3: 'num_hawker_2km'})

# Reset the index of the DataFrame and drop the old index column
flat_hawker = flat_hawker.reset_index().drop('index', axis=1)

# Display the first few rows of the DataFrame to review the data
flat_hawker.head()

flat  hawker hawker_dist num_hawker_2km
0    580 woodlands dr 16  731628    0.703451              3
1  556 ang mo kio ave 10  560528    0.310949              5
2  226b compassvale walk  530328    2.119392              0
3         41 stirling rd  141003    0.443999             13
4     238 tampines st 21  521106    0.915742              3

In [29]:
# Save the 'flat_hawker' DataFrame to a CSV file named 'flat_hawker_csv.csv' at the specified file path
# The 'index=False' parameter ensures that the row index is not included in the output CSV file
flat_hawker.to_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_hawker.csv', index=False)

In [30]:
# Load the dataset from the specified file path into a DataFrame named 'shop'
# This dataset contains information about shopping malls
# The 'encoding' parameter is set to 'cp1252' to correctly handle character encoding in the file
shop = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/shoppingmall.csv', encoding='cp1252')

# Display the first few rows of the DataFrame to review the structure and contents of the shopping mall data
shop.head()

Mall Name
0           100 AM
1     313@Somerset
2     321 Clementi
3        888 Plaza
4  Admiralty Place

In [31]:
# Extract the 'Mall Name' column from the 'shop' DataFrame into a list named 'shop_name'
# This list contains the names of all shopping malls from the dataset
shop_name = list(shop['Mall Name'])

# Create a list of unique shopping mall names by converting 'shop_name' to a set (which removes duplicates)
# and then converting it back to a list
unique_shop_name = list(set(shop_name))

# Print the number of unique shopping mall names found in the dataset
# This helps to determine how many distinct shopping malls are represented
print('Unique addresses:', len(unique_shop_name))

Unique addresses: 174


In [32]:
# Call the 'find_postal' function with the list of unique shopping mall names ('unique_shop_name')
# and save the resulting data (including postal codes and geographical coordinates) 
# to a CSV file named 'shoppingmall.csv' in the specified directory.
find_postal(unique_shop_name, 'C:/Users/Bwah/Desktop/488 Dataset/shoppingmall.csv')

0 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Katong Shopping Centre
1 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Funan
2 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=The Clementi Mall
3 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Elias Mall


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The

4 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Pioneer Mall
5 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Rivervale Plaza
6 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Buangkok Square
7 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Aperia


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


8 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Changi City Point
9 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Oasis Terraces
10 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Wisteria Mall


...

C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


163 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Wisma Atria
164 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=The Paragon
165 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=The Poiz
166 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Djitsun Mall Bedok


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


167 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Heartland Mall
168 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Balestier Hill Shopping Centre
169 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=myVillage At Serangoon Garden
170 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Orchard Plaza
171 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Rivervale Mall
172 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Greenridge Shopping Centre
173 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Westgate


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


In [33]:
# Load the dataset from the specified file path into a DataFrame named 'shop_coord'
# This dataset contains information about shopping malls, including postal codes and coordinates
shop_coord = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/shoppingmall.csv.csv')

# Remove duplicate rows based on the 'POSTAL' column to ensure that each postal code is unique
shop_coord.drop_duplicates(subset=['ADDRESS'], inplace=True)

# Select only the relevant columns: 'address', 'LATITUDE', and 'LONGITUDE'
# This keeps only the address and its associated latitude and longitude coordinates
shop_coord = shop_coord[['address', 'LATITUDE', 'LONGITUDE']]

# Display the first few rows of the updated DataFrame to check the data
shop_coord.head()

address  LATITUDE   LONGITUDE
0  Katong Shopping Centre  1.303820  103.901040
1  Katong Shopping Centre  1.304097  103.901516
2  Katong Shopping Centre  1.303798  103.901162
3                   Funan  1.291348  103.849990
4                   Funan  1.291373  103.850282

In [34]:
# Use the 'find_nearest' function to find the nearest shopping mall for each flat in 'flat_coord'
# The function returns a dictionary where each key is a flat address and the value contains information about the nearest mall
nearest_mall = find_nearest(flat_coord, shop_coord)

# Convert the dictionary returned by 'find_nearest' into a DataFrame
# The DataFrame is transposed to align the dictionary keys with DataFrame columns
flat_mall = pd.DataFrame.from_dict(nearest_mall).T

# Rename the columns of the DataFrame for better readability
# The columns are renamed to: 'flat', 'mall', 'mall_dist', and 'num_mall_2km'
flat_mall = flat_mall.rename(columns={0: 'flat', 1: 'mall', 2: 'mall_dist', 3: 'num_mall_2km'})

# Reset the index of the DataFrame and drop the old index column
flat_mall = flat_mall.reset_index().drop('index', axis=1)

# Display the first few rows of the DataFrame to review the data
flat_mall.head()

flat                  mall mall_dist num_mall_2km
0    580 woodlands dr 16           Vista Point  0.242819            8
1  556 ang mo kio ave 10  eople's Park Complex  0.910053            1
2  226b compassvale walk       Rivervale Plaza  0.377353           16
3         41 stirling rd                   IMM  0.991172            1
4     238 tampines st 21            Tampines 1  0.076621           27

In [35]:
# Save the 'flat_mall' DataFrame to a CSV file named 'flat_mall.csv' at the specified file path
# The 'index=False' parameter ensures that the row index is not included in the output CSV file
flat_mall.to_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_mall.csv', index=False)

In [36]:
# Load the dataset from the specified file path into a DataFrame named 'park'
# This dataset contains information about parks, including their details and locations
# The 'encoding' parameter is set to 'cp1252' to correctly handle character encoding in the file
park = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/parks.csv', encoding='cp1252')

# Display the first few rows of the DataFrame to review the structure and contents of the park data
park.head()

park name
0          Admiralty Park
1               Aida Park
2           Aljunied Park
3  Ang Mo Kio Linear Park
4     Ann Siang Hill Park

In [37]:
# Extract the 'park name' column from the 'park' DataFrame into a list named 'park_name'
# This list contains the names of all parks from the dataset
park_name = list(park['park name'])

# Create a list of unique park names by converting 'park_name' to a set (which removes duplicates)
# and then converting it back to a list
unique_park_name = list(set(park_name))

# Print the number of unique park names found in the dataset
# This helps to determine how many distinct parks are represented
print('Unique addresses:', len(unique_park_name))

Unique addresses: 195


In [38]:
# Call the 'find_postal' function with the list of unique park names ('unique_park_name')
# and save the resulting data (including postal codes and geographical coordinates) 
# to a CSV file named 'parks.csv' in the specified directory.
find_postal(unique_park_name, 'C:/Users/Bwah/Desktop/488 Dataset/parks.csv')

0 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Lengkong Enam Park
1 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Novena Park
2 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Choa Chu Kang Park
3 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Kallang Riverside Park


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The

4 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Sennett Linear Park
5 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Tanah Puteh Park
6 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Lorong Marican Park
7 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Lorong N Telok Kurau Park
8 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Lower Peirce Reservoir Park


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


9 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Brooks Park
10 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Sungei Api Api Park
11 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Eastwood Park Playground
12 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Bangsawan Park


...

C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


185 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Telok Blangah Hill Park
186 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Hazel Park Open Space
187 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Wilkinson Interim Park
188 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Punggol Waterway Park


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


189 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Savoy Park Playground
190 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Lorong Marzuki Park
191 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Dairy Farm Nature Park
192 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Chiltern Drive Interim Park
193 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=East Coast Park
194 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=Carpmael Park


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


In [39]:
# Load the dataset containing park coordinates from the specified file path into a DataFrame named 'park_coord'
# This dataset includes addresses, latitude, and longitude information for parks
park_coord = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/parks.csv.csv')

# Remove duplicate rows based on the 'address' column to ensure each park address is unique
park_coord.drop_duplicates(subset=['address'], inplace=True)

# Select only the relevant columns: 'address', 'LATITUDE', and 'LONGITUDE'
# This filters the DataFrame to keep only the necessary geographic information
park_coord = park_coord[['address', 'LATITUDE', 'LONGITUDE']]

# Display the first few rows of the updated DataFrame to review the data
park_coord.head()

address  LATITUDE   LONGITUDE
0      Lengkong Enam Park  1.327428  103.914725
1             Novena Park  1.322292  103.842819
3      Choa Chu Kang Park  1.392232  103.748795
6  Kallang Riverside Park  1.307230  103.868326
7     Sennett Linear Park  1.317581  103.935964

In [40]:
# Use the 'find_nearest' function to find the nearest park for each flat in 'flat_coord'
# The function returns a dictionary where each key is a flat address and the value contains information about the nearest park
nearest_park = find_nearest(flat_coord, park_coord)

# Convert the dictionary returned by 'find_nearest' into a DataFrame
# Transpose the DataFrame to align the dictionary keys with DataFrame columns
flat_park = pd.DataFrame.from_dict(nearest_park).T

# Rename the columns of the DataFrame for better readability
# The columns are renamed to: 'flat', 'park', 'park_dist', and 'num_park_2km'
flat_park = flat_park.rename(columns={0: 'flat', 1: 'park', 2: 'park_dist', 3: 'num_park_2km'})

# Reset the index of the DataFrame and drop the old index column
flat_park = flat_park.reset_index().drop('index', axis=1)

# Display the first few rows of the DataFrame to review the data
flat_park.head()

flat                      park park_dist num_park_2km
0    580 woodlands dr 16  Woodlands Town Park East  2.010897            0
1  556 ang mo kio ave 10           Nim Meadow Park  0.968388            2
2  226b compassvale walk   Sengkang Riverside Park  2.123911            0
3         41 stirling rd            one-north Park  1.335116            0
4     238 tampines st 21            Sun Plaza Park  0.471349            1

In [41]:
# Save the 'flat_park' DataFrame to a CSV file named 'flat_park.csv'
# The file will be saved in the specified directory
# The 'index=False' parameter ensures that the DataFrame's row index is not included in the output CSV file
flat_park.to_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_park.csv', index=False)

In [42]:
# Load the dataset containing MRT station information from the specified file path into a DataFrame named 'mrt'
# This dataset includes details about MRT stations, and the 'encoding' parameter is set to 'cp1252' to handle character encoding
mrt = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/mrtsg.csv', encoding='cp1252')

# Display the first few rows of the DataFrame to review the structure and contents of the MRT station data
mrt.head()

STN NAME STN_NO   COLOR
0   ADMIRALTY MRT STATION   NS10     RED
1    ALJUNIED MRT STATION    EW9   GREEN
2  ANG MO KIO MRT STATION   NS16     RED
3       BAKAU LRT STATION    SE3  OTHERS
4     BANGKIT LRT STATION    BP9  OTHERS

In [43]:
# Extract the 'STN NAME' column from the 'mrt' DataFrame into a list named 'mrt_name'
# This list contains the names of all MRT stations from the dataset
mrt_name = list(mrt['STN NAME'])

# Create a list of unique MRT station names by converting 'mrt_name' to a set (which removes duplicates)
# and then converting it back to a list
unique_mrt_name = list(set(mrt_name))

# Print the number of unique MRT station names found in the dataset
# This helps to determine how many distinct MRT stations are represented
print('Unique addresses:', len(unique_mrt_name))

Unique addresses: 166


In [44]:
# Call the 'find_postal' function with the list of unique MRT station names ('unique_mrt_name')
# and specify the output file path where the results will be saved ('mrtsg.csv')
# This function will find and append postal codes and geographical coordinates for each MRT station
find_postal(unique_mrt_name, 'C:/Users/Bwah/Desktop/488 Dataset/mrtsg.csv')

0 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=LAYAR LRT STATION
1 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=TELOK AYER MRT STATION
2 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BARTLEY MRT STATION
3 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=OASIS LRT STATION


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


4 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=LAKESIDE MRT STATION
5 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=CHENG LIM LRT STATION
6 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=CORAL EDGE LRT STATION
7 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=PAYA LEBAR MRT STATION


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


8 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BUKIT PANJANG LRT STATION
9 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BEDOK NORTH MRT STATION
10 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=KUPANG LRT STATION
11 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=COMPASSVALE LRT STATION


...

C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


155 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BUKIT BROWN MRT STATION
156 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=SERANGOON MRT STATION
157 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BOON KENG MRT STATION
158 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=CLARKE QUAY MRT STATION


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


159 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=TUAS WEST ROAD MRT STATION
160 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=MOUNTBATTEN MRT STATION
161 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=KRANJI MRT STATION
162 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=RENJONG LRT STATION
163 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=CHOA CHU KANG LRT STATION
164 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=TELOK BLANGAH MRT STATION
165 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=PUNGGOL POINT LRT STATION


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


In [45]:
# Load the dataset containing MRT station coordinates from the specified CSV file into a DataFrame named 'mrt_coord'
# The file path should be checked to ensure it is correct, as it includes an extra '.csv'
mrt_coord = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/mrtsg.csv.csv')

# Remove duplicate rows based on the 'address' column to ensure each address appears only once in the DataFrame
mrt_coord.drop_duplicates(subset=['address'], inplace=True)

# Select and retain only the 'address', 'LATITUDE', and 'LONGITUDE' columns for further analysis
mrt_coord = mrt_coord[['address','LATITUDE','LONGITUDE']]

# Display the first few rows of the DataFrame to review the structure and content of the MRT station coordinates
mrt_coord.head()

address  LATITUDE   LONGITUDE
0        LAYAR LRT STATION  1.392080  103.880030
1   TELOK AYER MRT STATION  1.282069  103.848649
5      BARTLEY MRT STATION  1.342445  103.880197
9        OASIS LRT STATION  1.402287  103.912727
10    LAKESIDE MRT STATION  1.344105  103.720302

In [46]:
# Find the nearest MRT stations for each flat using the 'find_nearest' function
# The 'flat_coord' DataFrame contains coordinates for flats, and 'mrt_coord' contains coordinates for MRT stations
nearest_mrt = find_nearest(flat_coord, mrt_coord)

# Convert the dictionary returned by 'find_nearest' into a DataFrame
# Transpose the DataFrame to adjust the format and create a structure suitable for further processing
flat_mrt = pd.DataFrame.from_dict(nearest_mrt).T

# Rename the columns of the DataFrame to meaningful names:
# - 'flat': Original flat address
# - 'mrt': Nearest MRT station address
# - 'mrt_dist': Distance to the nearest MRT station
# - 'num_mrt_2km': Number of MRT stations within a 2 km radius
flat_mrt = flat_mrt.rename(columns={0: 'flat', 1: 'mrt', 2: 'mrt_dist', 3: 'num_mrt_2km'})

# Reset the index of the DataFrame and drop the old index column to tidy up the DataFrame structure
flat_mrt = flat_mrt.reset_index().drop('index', axis=1)

# Display the first few rows of the DataFrame to review the structure and contents of the MRT-related information
flat_mrt.head()

flat                          mrt  mrt_dist num_mrt_2km
0    580 woodlands dr 16  WOODLANDS SOUTH MRT STATION  0.486444           1
1  556 ang mo kio ave 10       ANG MO KIO MRT STATION  0.927321           1
2  226b compassvale walk         RANGGUNG LRT STATION  0.450487          10
3         41 stirling rd     COMMONWEALTH MRT STATION  0.594058           2
4     238 tampines st 21    TAMPINES EAST MRT STATION  0.897344           2

In [47]:
# Save the 'flat_mrt' DataFrame to a CSV file named 'flat_mrt.csv'
# The file will be saved in the specified directory
# The 'index=False' parameter ensures that the DataFrame's row index is not included in the output CSV file
flat_mrt.to_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_mrt.csv', index=False)

In [48]:
# Load the dataset containing bus information from the specified CSV file into a DataFrame named 'bus'
# The file path provided should be correct, pointing to the location of the CSV file
bus = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/bus.csv')

# Display the first few rows of the DataFrame to review the structure and content of the bus information
bus.head()

bus location
0   ang mo kio interchange
1        bedok interchange
2       bishan interchange
3     boon lay interchange
4  bukit batok interchange

In [49]:
# Extract the 'bus location' column from the 'bus' DataFrame and convert it into a list named 'bus_name'
# This list contains all bus locations as strings
bus_name = list(bus['bus location'])

# Remove duplicate entries by converting the list to a set and then back to a list
# This gives 'unique_bus_name', which contains only unique bus locations
unique_bus_name = list(set(bus_name))

# Print the number of unique bus locations found in the dataset
print('Unique addresses:', len(unique_bus_name))

Unique addresses: 42


In [50]:
# Call the 'find_postal' function with the list of unique bus locations ('unique_bus_name')
# and specify the output file path ('bus.csv') where the results will be saved
# This function will find and append postal codes and geographical coordinates for each bus location
find_postal(unique_bus_name, 'C:/Users/Bwah/Desktop/488 Dataset/bus.csv')

0 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=bukit merah interchange
1 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=jurong east interchange
2 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=boon lay interchange
3 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=shenton way terminal


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


4 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=joo koon interchange
5 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=bishan interchange
6 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=kampong bahru terminal
7 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=lor 1 geylang terminal


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


8 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=st. michael's terminal
9 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=punggol temp interchange
10 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=kent ridge terminal
11 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=serangoon interchange


...

C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


36 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=upp east coast terminal
37 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=tampines concourse interchange
38 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=larkin terminal
39 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=tuas terminal


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


40 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=tampines interchange
41 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=bedok interchange


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


In [51]:
# Load the dataset containing bus coordinates from the specified CSV file into a DataFrame named 'bus_coord'
# The file path should be checked for correctness (note the double '.csv' in the file name which might be an error)
bus_coord = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/bus.csv.csv')

# Remove duplicate rows based on the 'address' column to ensure each address is unique in the DataFrame
bus_coord.drop_duplicates(subset=['address'], inplace=True)

# Select only the relevant columns: 'address', 'LATITUDE', and 'LONGITUDE'
# This creates a DataFrame containing only the necessary information for bus locations
bus_coord = bus_coord[['address','LATITUDE','LONGITUDE']]

# Display the first few rows of the DataFrame to review the structure and content of the bus coordinates data
bus_coord.head()

address  LATITUDE   LONGITUDE
0   bukit merah interchange  1.282040  103.817210
1   jurong east interchange  1.331864  103.740927
5      boon lay interchange  1.339315  103.705351
9      shenton way terminal  1.274486  103.847595
10     joo koon interchange  1.327162  103.678279

In [52]:
# Find the nearest bus locations for each flat using the 'find_nearest' function
# 'flat_coord' contains coordinates of flats and 'bus_coord' contains coordinates of bus locations
nearest_bus = find_nearest(flat_coord, bus_coord)

# Convert the dictionary returned by 'find_nearest' into a DataFrame
# The DataFrame will have flats as rows and their corresponding nearest bus data as columns
flat_bus = pd.DataFrame.from_dict(nearest_bus).T

# Rename the columns to more descriptive names:
# 0 -> 'flat': the flat address,
# 1 -> 'bus': the nearest bus location,
# 2 -> 'bus_dist': distance to the nearest bus,
# 3 -> 'num_bus_2km': number of buses within 2km radius
flat_bus = flat_bus.rename(columns={0: 'flat', 1: 'bus', 2: 'bus_dist', 3: 'num_bus_2km'}).reset_index().drop('index', axis=1)

# Display the first few rows of the DataFrame to review the results
flat_bus.head()

flat                      bus  bus_dist num_bus_2km
0    580 woodlands dr 16    woodlands interchange   1.33668           0
1  556 ang mo kio ave 10   ang mo kio interchange  1.056927           0
2  226b compassvale walk  compassvale interchange  0.446217           3
3         41 stirling rd     buona vista terminal  1.559862           0
4     238 tampines st 21     tampines interchange  0.363718           2

In [53]:
# Save the 'flat_bus' DataFrame to a CSV file named 'flat_bus.csv'
# The file will be saved in the specified directory
# The 'index=False' parameter ensures that the DataFrame's row index is not included in the output CSV file
flat_bus.to_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_bus.csv', index=False)

In [54]:
# Load the dataset containing car park information from the specified CSV file into a DataFrame named 'carpark'
# The file path is provided, and the first few rows of the DataFrame are displayed for initial inspection
carpark = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/HDBCarparkInformation.csv')

# Display the first few rows of the DataFrame to review the structure and content of the car park information
carpark.head()

car_park_no                                      address     x_coord  \
0         ACB  BLK 270/271 ALBERT CENTRE BASEMENT CAR PARK  30314.7936   
1         ACM                    BLK 98A ALJUNIED CRESCENT  33758.4143   
2         AH1                          BLK 101 JALAN DUSUN  29257.7203   
3        AK19               BLOCK 253 ANG MO KIO STREET 21  28185.4359   
4        AK31             BLK 302/348 ANG MO KIO STREET 31  29482.0290   

      y_coord          car_park_type type_of_parking_system  \
0  31490.4942      BASEMENT CAR PARK     ELECTRONIC PARKING   
1  33695.5198  MULTI-STOREY CAR PARK     ELECTRONIC PARKING   
2  34500.3599       SURFACE CAR PARK     ELECTRONIC PARKING   
3  39012.6664       SURFACE CAR PARK         COUPON PARKING   
4  38684.1754       SURFACE CAR PARK         COUPON PARKING   

  short_term_parking             free_parking night_parking  car_park_decks  \
0          WHOLE DAY                       NO           YES               1   
1          WHOLE DAY  SUN & PH FR 7AM-10.30PM           YES               5   
2          WHOLE DAY  SUN & PH FR 7AM-10.30PM           YES               0   
3            7AM-7PM                       NO            NO               0   
4                 NO                       NO            NO               0   

   gantry_height car_park_basement  
0            1.8                 Y  
1            2.1                 N  
2            0.0                 N  
3            0.0                 N  
4            0.0                 N

In [55]:
# Extract the 'address' column from the 'carpark' DataFrame and convert it into a list named 'carpark_name'
# This list contains all car park addresses from the dataset
carpark_name = list(carpark['address'])

# Remove duplicate addresses by converting the list to a set and then back to a list
# This creates a list of unique car park addresses
unique_carpark_name = list(set(carpark_name))

# Print the number of unique car park addresses to verify how many distinct car park locations are present
print('Unique addresses:', len(unique_carpark_name))

Unique addresses: 2219


In [56]:
# Use the 'find_postal' function to obtain postal codes and geographical coordinates for each unique car park address
# 'unique_carpark_name' contains the list of unique car park addresses
# The results are saved in the specified CSV file path 'C:/Users/Bwah/Desktop/488 Dataset/HDBCarparkInformation.csv'
find_postal(unique_carpark_name, 'C:/Users/Bwah/Desktop/488 Dataset/HDBCarparkInformation.csv')

0 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 166 BUKIT BATOK WEST AVENUE 8
1 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 404A BUKIT BATOK WEST AVENUE 7
2 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 229/230 ANG MO KIO STREET 22
3 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 232/233 ANG MO KIO STREET 22


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


4 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 681/682 RACE COURSE ROAD
5 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 109 BIDADARI PARK DRIVE
6 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 503/504 BISHAN STREET 11
7 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 19A DOVER CRESCENT


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


8 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 677 PUNGGOL DRIVE
9 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 215 ANG MO KIO STREET 22
10 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 531/536 SERANGOON NORTH AVENUE 4
11 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 941A HOUGANG STREET 92


...

2210 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=DEFU LANE 11
2211 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLKS 556/557 BEDOK NORTH STREET 3
2212 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 116/122 LORONG 1 TOA PAYOH
2213 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 321-322,324-326 CLEMENTI AVENUE 5


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


2214 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 88 TANGLIN HALT ROAD
2215 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 109/117 TECK WHYE LANE
2216 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 988 BUANGKOK GREEN
2217 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 201/206 CLEMENTI AVENUE 6


C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)
C:\Users\Bwah\AppData\Local\Temp\ipykernel_8692\2276470172.py:38: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  file = file.append(temp_df)


2218 https://www.onemap.gov.sg/api/common/elastic/search?&returnGeom=Y&getAddrDetails=Y&pageNum=1&searchVal=BLK 775-794 YISHUN RING RD/AVENUE 2


In [57]:
# Load the car park coordinates data from the specified CSV file into a DataFrame named 'carpark_coord'
# This file contains postal codes and geographical coordinates for car park addresses
carpark_coord = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/HDBCarparkInformation.csv.csv')

# Remove duplicate entries based on the 'address' column to ensure each address appears only once
carpark_coord.drop_duplicates(subset=['address'], inplace=True)

# Select only the 'address', 'LATITUDE', and 'LONGITUDE' columns from the DataFrame
# This retains only the relevant columns for further analysis
carpark_coord = carpark_coord[['address', 'LATITUDE', 'LONGITUDE']]

# Display the first few rows of the DataFrame to review the structure and content of the car park coordinates data
carpark_coord.head()

address  LATITUDE   LONGITUDE
0    BLK 166 BUKIT BATOK WEST AVENUE 8  1.347153  103.742825
10  BLK 404A BUKIT BATOK WEST AVENUE 7  1.358924  103.742198
20    BLK 229/230 ANG MO KIO STREET 22  1.368778  103.840274
30    BLK 232/233 ANG MO KIO STREET 22  1.368778  103.840274
40        BLK 681/682 RACE COURSE ROAD  1.315248  103.857397

In [58]:
# Find the nearest car parks to each flat using the 'find_nearest' function
# 'flat_coord' contains coordinates of flats, and 'carpark_coord' contains coordinates of car parks
nearest_carpark = find_nearest(flat_coord, carpark_coord)

# Convert the dictionary returned by 'find_nearest' into a DataFrame for easier manipulation
# The DataFrame is transposed with '.T' to switch rows and columns
flat_carpark = pd.DataFrame.from_dict(nearest_carpark).T

# Rename columns for clarity:
# 0: 'flat' - the address of the flat
# 1: 'carpark' - the address of the nearest car park
# 2: 'carpark_dist' - distance to the nearest car park
# 3: 'num_carpark_2km' - number of car parks within 2km radius
flat_carpark = flat_carpark.rename(columns={0: 'flat', 1: 'carpark', 2: 'carpark_dist', 3: 'num_carpark_2km'})

# Reset the index and drop the old index column to maintain a clean DataFrame structure
flat_carpark = flat_carpark.reset_index().drop('index', axis=1)

# Display the first few rows of the DataFrame to review the results of the nearest car park calculations
flat_carpark.head()

flat                                     carpark  \
0    580 woodlands dr 16                 BLK 579A WOODLANDS DRIVE 16   
1  556 ang mo kio ave 10  BLK 269/269A/269B CHENG YAN COURT CAR PARK   
2  226b compassvale walk                   BLK 224E COMPASSVALE WALK   
3         41 stirling rd                        BLK 49 STIRLING ROAD   
4     238 tampines st 21                  BLK 507 TAMPINES CENTRAL 1   

  carpark_dist num_carpark_2km  
0     0.098452              50  
1      0.27145               7  
2     0.148239              62  
3     0.130279              52  
4     0.096046              57

In [59]:
# Save the DataFrame 'flat_carpark' to a CSV file
# The file will be saved at the specified path with the name 'flat_carpark.csv'
# 'index=False' ensures that the DataFrame's index is not included in the CSV file
flat_carpark.to_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_carpark.csv', index=False)

In [60]:
# Merge multiple DataFrames on the 'flat' column
# The merging is performed using an outer join to ensure that all rows from each DataFrame are included

# Merge 'flat_school' with 'flat_hawker' on the 'flat' column
flat_amenities = flat_school.merge(flat_hawker, on='flat', how='outer')

# Merge the resulting DataFrame with 'flat_park' on the 'flat' column
flat_amenities = flat_amenities.merge(flat_park, on='flat', how='outer')

# Continue merging with 'flat_mall'
flat_amenities = flat_amenities.merge(flat_mall, on='flat', how='outer')

# Merge with 'flat_mrt'
flat_amenities = flat_amenities.merge(flat_mrt, on='flat', how='outer')

# Merge with 'flat_bus'
flat_amenities = flat_amenities.merge(flat_bus, on='flat', how='outer')

# Merge with 'flat_carpark'
flat_amenities = flat_amenities.merge(flat_carpark, on='flat', how='outer')

# Merge with 'flat_supermarket'
flat_amenities = flat_amenities.merge(flat_supermarket, on='flat', how='outer')

# Display the first few rows of the final merged DataFrame to verify the result
flat_amenities.head()

flat                      school school_dist  \
0    580 woodlands dr 16  WOODGROVE SECONDARY SCHOOL    0.251862   
1  556 ang mo kio ave 10    JING SHAN PRIMARY SCHOOL    0.611724   
2  226b compassvale walk  SENG KANG SECONDARY SCHOOL    0.161496   
3         41 stirling rd  QUEENSWAY SECONDARY SCHOOL    0.177472   
4     238 tampines st 21  PASIR RIS SECONDARY SCHOOL    0.313643   

  num_school_2km  hawker hawker_dist num_hawker_2km                      park  \
0              8  731628    0.703451              3  Woodlands Town Park East   
1              3  560528    0.310949              5           Nim Meadow Park   
2              9  530328    2.119392              0   Sengkang Riverside Park   
3              3  141003    0.443999             13            one-north Park   
4              7  521106    0.915742              3            Sun Plaza Park   

  park_dist num_park_2km  ... num_mrt_2km                      bus  bus_dist  \
0  2.010897            0  ...           1    woodlands interchange   1.33668   
1  0.968388            2  ...           1   ang mo kio interchange  1.056927   
2  2.123911            0  ...          10  compassvale interchange  0.446217   
3  1.335116            0  ...           2     buona vista terminal  1.559862   
4  0.471349            1  ...           2     tampines interchange  0.363718   

  num_bus_2km                                     carpark carpark_dist  \
0           0                 BLK 579A WOODLANDS DRIVE 16     0.098452   
1           0  BLK 269/269A/269B CHENG YAN COURT CAR PARK      0.27145   
2           3                   BLK 224E COMPASSVALE WALK     0.148239   
3           0                        BLK 49 STIRLING ROAD     0.130279   
4           2                  BLK 507 TAMPINES CENTRAL 1     0.096046   

  num_carpark_2km supermarket supermarket_dist num_supermarket_2km  
0              50      730548         0.246302                   3  
1               7      560525         0.411332                   3  
2              62      540118         0.385921                   6  
3              52      141088         0.540076                   3  
4              57      520506         0.075366                   7  

[5 rows x 25 columns]

In [61]:
# Save the 'flat_amenities' DataFrame to a CSV file
# The file will be saved at the specified path with the name 'flat_amenities.csv'
# 'index=False' ensures that the DataFrame's index is not included in the CSV file
flat_amenities.to_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_amenities.csv', index=False)

In [62]:
import pandas as pd

# Load the 'flat_amenities' DataFrame from a CSV file
# This file contains information about amenities for each flat
flat_amenities = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/flat_amenities.csv')

# Load the 'prices' DataFrame from a CSV file
# This file contains the pricing information for each flat
prices = pd.read_csv('C:/Users/Bwah/Desktop/488 Dataset/output3.0 grouped region + expanded storey.csv')

# Display summary information about the 'prices' DataFrame, including data types and non-null counts
prices.info()

flat_amenities.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2810792 entries, 0 to 2810791
Data columns (total 16 columns):
 #   Column               Dtype  
---  ------               -----  
 0   address              object 
 1   month                object 
 2   town                 object 
 3   flat_type            object 
 4   block                object 
 5   street_name          object 
 6   storey_range         object 
 7   floor_area_sqm       float64
 8   flat_model           object 
 9   lease_commence_date  int64  
 10  resale_price         int64  
 11  remaining_lease      int64  
 12  flat_group           object 
 13  region               object 
 14  mature               object 
 15  storey               int64  
dtypes: float64(1), int64(4), object(11)
memory usage: 343.1+ MB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9841 entries, 0 to 9840
Data columns (total 25 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0 

In [63]:
# Rename the 'flat' column to 'address' in 'flat_amenities' DataFrame to match with 'prices' DataFrame
flat_amenities = flat_amenities.rename(columns={'flat': 'address'})

# Merge 'flat_amenities' DataFrame with 'prices' DataFrame on the 'address' column
# 'how="outer"' ensures that all records from both DataFrames are included, even if there are no matching records
flat_amenities = flat_amenities.merge(prices, on='address', how='outer')

# Display the first few rows of the merged 'flat_amenities' DataFrame to inspect the results
flat_amenities.head()

# Display summary information about the merged 'flat_amenities' DataFrame
flat_amenities.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2810792 entries, 0 to 2810791
Data columns (total 40 columns):
 #   Column               Dtype  
---  ------               -----  
 0   address              object 
 1   school               object 
 2   school_dist          float64
 3   num_school_2km       int64  
 4   hawker               object 
 5   hawker_dist          float64
 6   num_hawker_2km       int64  
 7   park                 object 
 8   park_dist            float64
 9   num_park_2km         int64  
 10  mall                 object 
 11  mall_dist            float64
 12  num_mall_2km         int64  
 13  mrt                  object 
 14  mrt_dist             float64
 15  num_mrt_2km          int64  
 16  bus                  object 
 17  bus_dist             float64
 18  num_bus_2km          int64  
 19  carpark              object 
 20  carpark_dist         float64
 21  num_carpark_2km      int64  
 22  supermarket          int64  
 23  supermarket_dist     float64
 24

In [70]:
# Create a duplicate of the 'flat_amenities' DataFrame and assign it to 'flatdrop'
flatdrop = flat_amenities.copy()

# Drop the specified columns from 'flatdrop':
# 'school', 'hawker', 'park', 'mall', 'mrt', 'bus', 'carpark', 'supermarket',
# 'storey_range', 'flat_model', 'address', 'street_name', and 'block'
# The 'axis=1' parameter ensures that the operation is performed on columns
flatdrop = flatdrop.drop(['school', 'hawker', 'park', 'mall', 'mrt', 'bus', 'carpark', 'supermarket',
                          'storey_range', 'flat_model', 'street_name', 'block'], axis=1)

# Display the columns of the resulting 'flat_amenities' DataFrame
flatdrop.columns

flatdrop.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2810792 entries, 0 to 2810791
Data columns (total 28 columns):
 #   Column               Dtype  
---  ------               -----  
 0   address              object 
 1   school_dist          float64
 2   num_school_2km       int64  
 3   hawker_dist          float64
 4   num_hawker_2km       int64  
 5   park_dist            float64
 6   num_park_2km         int64  
 7   mall_dist            float64
 8   num_mall_2km         int64  
 9   mrt_dist             float64
 10  num_mrt_2km          int64  
 11  bus_dist             float64
 12  num_bus_2km          int64  
 13  carpark_dist         float64
 14  num_carpark_2km      int64  
 15  supermarket_dist     float64
 16  num_supermarket_2km  int64  
 17  month                object 
 18  town                 object 
 19  flat_type            object 
 20  floor_area_sqm       float64
 21  lease_commence_date  int64  
 22  resale_price         int64  
 23  remaining_lease      int64  
 24

In [65]:
# Create a duplicate of the 'flatdrop' DataFrame to work with
flat_sample = flatdrop.copy()

# Extract the year from the 'month' column by taking the first 4 characters
# and store it in a new 'year' column
flat_sample['year'] = flat_sample['month'].str[:4]

# Filter the DataFrame to include only rows where the 'year' is between 2010 and 2023
flat_sample = flat_sample[(flat_sample['year'] >= '2010') & (flat_sample['year'] <= '2023')]

# Drop the temporary 'year' column as it is no longer needed
flat_sample = flat_sample.drop(columns=['year'])

In [66]:
# Display the summary of the DataFrame `flat_sample`
# This includes the number of rows, column names, non-null counts, and data types for each column.
flat_sample.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 970169 entries, 66 to 2810791
Data columns (total 28 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   address              970169 non-null  object 
 1   school_dist          970169 non-null  float64
 2   num_school_2km       970169 non-null  int64  
 3   hawker_dist          970169 non-null  float64
 4   num_hawker_2km       970169 non-null  int64  
 5   park_dist            970169 non-null  float64
 6   num_park_2km         970169 non-null  int64  
 7   mall_dist            970169 non-null  float64
 8   num_mall_2km         970169 non-null  int64  
 9   mrt_dist             970169 non-null  float64
 10  num_mrt_2km          970169 non-null  int64  
 11  bus_dist             970169 non-null  float64
 12  num_bus_2km          970169 non-null  int64  
 13  carpark_dist         970169 non-null  float64
 14  num_carpark_2km      970169 non-null  int64  
 15  supermarket_dis

In [67]:
# Save the DataFrame `flat_sample` to a CSV file named 'output4.0.csv'
# The `index=False` parameter ensures that the index is not included as a separate column in the CSV file.
flat_sample.to_csv('output4.0 sample.csv', index=False)

In [68]:
# Save the DataFrame `flat_sample` to a CSV file named 'output4.0.csv'
# The `index=False` parameter ensures that the index is not included as a separate column in the CSV file.
flatdrop.to_csv('output4.0.csv', index=False)

In [69]:
flatdrop.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2810792 entries, 0 to 2810791
Data columns (total 28 columns):
 #   Column               Dtype  
---  ------               -----  
 0   address              object 
 1   school_dist          float64
 2   num_school_2km       int64  
 3   hawker_dist          float64
 4   num_hawker_2km       int64  
 5   park_dist            float64
 6   num_park_2km         int64  
 7   mall_dist            float64
 8   num_mall_2km         int64  
 9   mrt_dist             float64
 10  num_mrt_2km          int64  
 11  bus_dist             float64
 12  num_bus_2km          int64  
 13  carpark_dist         float64
 14  num_carpark_2km      int64  
 15  supermarket_dist     float64
 16  num_supermarket_2km  int64  
 17  month                object 
 18  town                 object 
 19  flat_type            object 
 20  floor_area_sqm       float64
 21  lease_commence_date  int64  
 22  resale_price         int64  
 23  remaining_lease      int64  
 24